---

# S03E07 : Fonctions & décorateurs - Décorateurs & classes

Cyril Desjouy

---

La dernière partie de cette série de notebook concerne les classes. Deux approches sont succinctement abordées :

* Décorer une classe
* Classe en tant que décorateur

## 1. Décorer une classe

Il existe deux approches différentes pour utiliser des décorateur sur une classe:

* décorer une méthode de la classe,
* décorer la classe elle-même.

### 1.1. Décorer les méthodes de classe

Python propose des décorateurs built-ins pour attribuer certaines propriétés à une méthode (Cf. saison ***classes & OOP***):

* `@staticmethod`: définit une méthode qui n'est pas liée à une instance particulière, 
* `@classmethod`: définit une méthode qui est liée à la classe,
* `@property`: permet de considérer une méthode comme un attribut.

Décorer une méthode est tout à fait similaire à décorer une fonction:

In [7]:
def prettier(func):
    def wrapper(*args, **kwargs):
        print('.oOO Processing OOo.'.center(80))
        results = func(*args, **kwargs)
        print('.oOO ~~~Done~~~ OOo.'.center(80))
        return results
    return wrapper

class DoThings:
    def __init__(self, task):
        self.task = task
    
    @prettier
    def do(self):
        print(f'Doing {self.task}!'.center(80))
        
thing = DoThings('maths')
thing.do()

                              .oOO Processing OOo.                              
                                  Doing maths!                                  
                              .oOO ~~~Done~~~ OOo.                              


### 1.2. Décorer la classe

Les décorateurs de classe sont très similaires aux décorateurs de fonctions. La seule différence est qu'ils prennent une classe en argument d'entrée, et non une fonction. 

Reprenons un exemple similaire au précédent pour illustrer ce principe:

In [27]:
@prettier
class DoThings:
    def __init__(self, task):
        self.task = task
        print('Creating instance of DoThings'.center(80))
    
    def do(self):
        print(f'Doing {self.task}!'.center(80))
        
thing = DoThings('maths')
thing.do()

                              .oOO Processing OOo.                              
                         Creating instance of DoThings                          
                              .oOO ~~~Done~~~ OOo.                              
                                  Doing maths!                                  


Lorsqu'il est appliqué à une classe, le décorateur agit uniquement à la création de l'instance. Tous les décorateurs que nous avons vu précédemment peuvent très bien être utilisés pour décorer une classe. Leur utilisation peut néanmoins conduire à des résultats inattendus comme illustré par l'exemple précédent.  Lorsque vous développez un décorateur, il s'agit de savoir au préalable s'il sera utilisé sur une fonction ou sur une classe. Son implémentation en dépendra!

## 2. Classes en tant que décorateur

Nous avons vu dans le notebook précédent comment garder trace de l'état d'un décorateur à l'aide des attributs de fonctions. Les classes peuvent faciliter un peu les choses. Considérons la classe suivante permettant d'illustrer le principe de création de classes décoratrices.

In [21]:
class Counter:
    def __init__(self):
        self.calls = 0

    def __call__(self):
        self.calls += 1
        print(f"Instance has been called {self.calls} times")
        
counter = Counter()
for i in range(3):
    counter()

Instance has been called 1 times
Instance has been called 2 times
Instance has been called 3 times


Rappelez-vous qu'écrire `@decorator` est juste une façon plus simple d'écrire `func = decorator(func)`. Par conséquent, si on a affaire à une classe, le décorateur doit prendre la fonction à décorer en argument d'entrée de sa méthode `__init__()`. Chaque instance de la classe doit de plus pouvoir être appelée pour qu'elle puisse agir sur la fonction à décorer.

On utilise ici donc classiquement la méthode spéciale `__call__` permettant de rendre ***callable*** chaque instance de la classe `Counter`. Cette méthode joue en fait le rôle du `wrapper` utilisé dans les fonctions décoratrices. Il ne nous manque plus qu'à passer la fonction à décorer à chaque instance de notre classe et le tour est joué!

**Note:** *On doit ici utiliser la fonction `functools.update_wrapper()` qui est équivalente au décorateur `@functools.wraps`.*

In [28]:
import functools

class Counter:
    def __init__(self, func):
        functools.update_wrapper(self, func)
        self.func = func
        self.calls = 0

    def __call__(self, *args, **kwargs):
        self.calls += 1
        print(f"Call {self.calls} of {self.func.__name__!r} function")
        return self.func(*args, **kwargs)

@Counter
def hello():
    print("Hello world!")
    
for i in range(3):
    hello()

Call 1 of 'hello' function
Hello world!
Call 2 of 'hello' function
Hello world!
Call 3 of 'hello' function
Hello world!


## Application 

<div class="alert alert-block alert-info">
Écrire un décorateur permettant de mesurer le temps qu'une fonction met à s'exécuter. 
Le décorateur gardera en mémoire une trace de tous les temps mesurés.
</div>
</div>

## Bibliographie

* [Real Python - Primer on Python decorators](https://realpython.com/primer-on-python-decorators/)
* [Geeksforgeeks - Class as decorators](https://www.geeksforgeeks.org/class-as-decorator-in-python)
* [Wiki Python.org - Decorators](https://wiki.python.org/moin/PythonDecorators)
* [Wiki Python.org - Decorator library](https://wiki.python.org/moin/PythonDecoratorLibrary)